## SECTION 0: IMPORT DATA

In [ ]:
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt
import seaborn as sns

In [ ]:
from google.colab import drive

drive.mount('/content/drive')


Mounted at /content/drive


In [ ]:
os.chdir('/content/drive/MyDrive/DATASCI210/data')

In [19]:
books_df = pd.read_pickle('books_data_clean.pkl')


In [21]:
# Set pandas to display full text without truncation
pd.set_option('display.max_colwidth', None)

unique_books = books_df[['title', 'preview_link']].drop_duplicates()
print(f"Found {len(unique_books)} unique book titles with preview links")

Found 71696 unique book titles with preview links


## Parallelized

In [33]:
import concurrent.futures
import requests
from requests.adapters import HTTPAdapter
import urllib3
from bs4 import BeautifulSoup
import re
import pandas as pd
import time
import os
from PIL import Image
from io import BytesIO
from tqdm.notebook import tqdm
from functools import partial

In [34]:
# Increase the connection pool limits
urllib3.connectionpool.DEFAULT_POOL_TIMEOUT = 100
urllib3.connectionpool.HTTPConnectionPool.maxsize = 25

In [35]:
def download_single_cover(row, output_folder="book_covers", session=None):
    """Download a single book cover image"""
    title = row['title']
    link = row['preview_link']

    # Use the provided session or create a new one
    if session is None:
        session = requests.Session()

    if not isinstance(link, str) or not link or not isinstance(title, str) or not title:
        return None

    try:
        # Create a safe filename from the title
        safe_title = re.sub(r'[^\w\-_]', '_', title)[:100]  # Limit length and replace unsafe chars

        # Extract book ID for the image URL
        book_id_match = re.search(r'id=([^&]+)', link)
        if not book_id_match:
            return {
                'title': title,
                'preview_link': link,
                'image_url': None,
                'image_path': None,
                'status': 'error: could not extract book ID'
            }

        book_id = book_id_match.group(1)

        # Extract domain
        domain_match = re.search(r'(https://[^/]+)', link)
        domain = domain_match.group(1) if domain_match else "https://books.google.com"

        # Construct image URL
        image_url = f"{domain}/books/content?id={book_id}&printsec=frontcover&img=1&zoom=1"

        # Download the image
        img_response = session.get(image_url)

        if img_response.status_code == 200:
            try:
                img = Image.open(BytesIO(img_response.content))
                img_path = os.path.join(output_folder, f"{safe_title}.jpg")
                img.save(img_path)

                return {
                    'title': title,
                    'book_id': book_id,
                    'preview_link': link,
                    'image_url': image_url,
                    'image_path': img_path,
                    'status': 'success'
                }
            except Exception as e:
                return {
                    'title': title,
                    'book_id': book_id,
                    'preview_link': link,
                    'image_url': image_url,
                    'image_path': None,
                    'status': f'error: {str(e)}'
                }
        else:
            return {
                'title': title,
                'book_id': book_id,
                'preview_link': link,
                'image_url': image_url,
                'image_path': None,
                'status': f'HTTP error: {img_response.status_code}'
            }

    except Exception as e:
        return {
            'title': title,
            'book_id': book_id if 'book_id' in locals() else 'unknown',
            'preview_link': link,
            'image_url': None,
            'image_path': None,
            'status': f'error: {str(e)}'
        }

def extract_book_covers_parallel(books_data, output_folder="book_covers", max_workers=16, batch_size=None):
    """
    Download book covers in parallel using ThreadPoolExecutor

    Parameters:
    books_data (DataFrame): DataFrame containing 'title' and 'preview_link' columns
    output_folder (str): Folder to save the images
    max_workers (int): Maximum number of concurrent workers
    batch_size (int): Optional batch size for processing large datasets

    Returns:
    DataFrame: Results of the download process
    """
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    all_results = []

    session = requests.Session()
    adapter = HTTPAdapter(pool_connections=25, pool_maxsize=25)
    session.mount('https://', adapter)
    session.mount('http://', adapter)

    download_func = partial(download_single_cover, output_folder=output_folder, session=session)

    # If batch_size is specified, process in batches
    if batch_size and len(books_data) > batch_size:
        num_batches = (len(books_data) + batch_size - 1) // batch_size

        for i in range(num_batches):
            start_idx = i * batch_size
            end_idx = min((i + 1) * batch_size, len(books_data))

            print(f"Processing batch {i+1}/{num_batches} (rows {start_idx} to {end_idx})")
            batch = books_data.iloc[start_idx:end_idx]

            batch_results = []
            with concurrent.futures.ThreadPoolExecutor(max_workers=max_workers) as executor:
                future_to_row = {executor.submit(download_func, row): idx
                                for idx, row in batch.iterrows()}

                for future in tqdm(concurrent.futures.as_completed(future_to_row),
                                  total=len(future_to_row)):
                    try:
                        result = future.result()
                        if result:
                            batch_results.append(result)
                    except Exception as e:
                        idx = future_to_row[future]
                        print(f"Error processing row {idx}: {e}")

            all_results.extend(batch_results)

            # Add a small delay between batches to avoid overwhelming the server
            if i < num_batches - 1:
                time.sleep(2)
    else:
        with concurrent.futures.ThreadPoolExecutor(max_workers=max_workers) as executor:
            future_to_row = {executor.submit(download_func, row): idx
                            for idx, row in books_data.iterrows()}

            for future in tqdm(concurrent.futures.as_completed(future_to_row),
                              total=len(future_to_row)):
                try:
                    result = future.result()
                    if result:
                        all_results.append(result)
                except Exception as e:
                    idx = future_to_row[future]
                    print(f"Error processing row {idx}: {e}")

    results_df = pd.DataFrame(all_results)

    # Calculate success rate
    success_count = len(results_df[results_df['status'] == 'success'])
    total_count = len(results_df)
    success_rate = (success_count / total_count) * 100 if total_count > 0 else 0

    print(f"\nDownload Summary:")
    print(f"Successfully downloaded: {success_count}/{total_count} ({success_rate:.2f}%)")

    return results_df

In [36]:
from multiprocessing import Pool

def extract_book_covers_multiprocess(books_data, output_folder="book_covers", processes=8):
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    # Convert DataFrame to list of dictionaries for multiprocessing
    books_list = books_data.to_dict('records')

    download_func = partial(download_single_cover, output_folder=output_folder)

    # Use process pool for parallelization
    with Pool(processes=processes) as pool:
        results = list(tqdm(pool.imap(download_func, books_list), total=len(books_list)))

    return pd.DataFrame([r for r in results if r is not None])

Use the functions

In [37]:
# Get unique combinations of title and preview link
unique_books = books_df[['title', 'preview_link']].drop_duplicates()
print(f"Found {len(unique_books)} unique book titles with preview links")

pd.set_option('display.max_colwidth', None)

# Extract book covers using parallel processing for ALL books
covers_df = extract_book_covers_parallel(
    unique_books,  # Using all unique books
    output_folder="book_covers",
    max_workers=16,
    batch_size=100  # Process in batches of 100 books
)

print(f"\nTotal books processed: {len(covers_df)}")
print(f"Successfully downloaded: {len(covers_df[covers_df['status'] == 'success'])}")
print(f"Failed downloads: {len(covers_df[covers_df['status'] != 'success'])}")

covers_df.head()

Found 71696 unique book titles with preview links
Processing batch 1/717 (rows 0 to 100)


  0%|          | 0/100 [00:00<?, ?it/s]

Processing batch 2/717 (rows 100 to 200)


  0%|          | 0/100 [00:00<?, ?it/s]

Processing batch 3/717 (rows 200 to 300)


...

  0%|          | 0/100 [00:00<?, ?it/s]

Processing batch 717/717 (rows 71600 to 71696)


  0%|          | 0/96 [00:00<?, ?it/s]


Download Summary:
Successfully downloaded: 71695/71696 (100.00%)

Total books processed: 71696
Successfully downloaded: 71695
Failed downloads: 1


title  \
0                              Pride & Prejudice (Penguin Classics)   
1                                             To Kill a Mockingbird   
2  The Hobbitt, or there and back again; illustrated by the author.   
3                                   Jane Eyre (Everyman's Classics)   
4                                                   OF MICE AND MEN   

        book_id  \
0  ZV9DDwAAQBAJ   
1  0NEbHGREK7cC   
2  Wbm1mQEACAAJ   
3  MsRAAQAAIAAJ   
4  nE_Si_bv-W4C   

                                                                                                                                    preview_link  \
0                                             http://books.google.com/books?id=ZV9DDwAAQBAJ&printsec=frontcover&dq=Pride&hl=&cd=1&source=gbs_api   
1                             http://books.google.com/books?id=0NEbHGREK7cC&printsec=frontcover&dq=To+Kill+a+Mockingbird&hl=&cd=1&source=gbs_api   
2     http://books.google.nl/books?id=Wbm1mQEACAAJ&dq=The+Hobbitt,+or+there+and+back+again%3B+illustrated+by+the+author.&hl=&cd=1&source=gbs_api   
3  http://books.google.nl/books?id=MsRAAQAAIAAJ&q=Jane+Eyre+(Everyman%27s+Classics)&dq=Jane+Eyre+(Everyman%27s+Classics)&hl=&cd=1&source=gbs_api   
4                                   http://books.google.com/books?id=nE_Si_bv-W4C&printsec=frontcover&dq=OF+MICE+AND+MEN&hl=&cd=1&source=gbs_api   

                                                                                 image_url  \
0  https://books.google.com/books/content?id=ZV9DDwAAQBAJ&printsec=frontcover&img=1&zoom=1   
1  https://books.google.com/books/content?id=0NEbHGREK7cC&printsec=frontcover&img=1&zoom=1   
2  https://books.google.com/books/content?id=Wbm1mQEACAAJ&printsec=frontcover&img=1&zoom=1   
3  https://books.google.com/books/content?id=MsRAAQAAIAAJ&printsec=frontcover&img=1&zoom=1   
4  https://books.google.com/books/content?id=nE_Si_bv-W4C&printsec=frontcover&img=1&zoom=1   

                                                                         image_path  \
0                              book_covers/Pride___Prejudice__Penguin_Classics_.jpg   
1                                             book_covers/To_Kill_a_Mockingbird.jpg   
2  book_covers/The_Hobbitt__or_there_and_back_again__illustrated_by_the_author_.jpg   
3                                   book_covers/Jane_Eyre__Everyman_s_Classics_.jpg   
4                                                   book_covers/OF_MICE_AND_MEN.jpg   

    status  
0  success  
1  success  
2  success  
3  success  
4  success

In [42]:
covers_df.to_pickle("book_covers_lookup.pkl")

In [39]:
import os
current_dir = os.getcwd()
print(f"Current working directory: {current_dir}")


Current working directory: /content/drive/MyDrive/DATASCI210/data
